<a href="https://colab.research.google.com/github/Bharath2/cube/blob/master/Soft_Actor_Critic.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!apt-get install -y xvfb python-opengl x11-utils > /dev/null 2>&1
!pip install pyvirtualdisplay > /dev/null 2>&1
!pip install mitdeeplearning
!pip install recordclass
!pip install box2d box2d-py box2d-kengz

  Using cached https://files.pythonhosted.org/packages/81/20/51d6c0c87f7642efb709c518fb0ca8e5eab068259588552c41da5926ae27/Box2D-kengz-2.3.3.tar.gz
  ERROR: Failed building wheel for box2d-kengz
  Running setup.py clean for box2d-kengz
Failed to build box2d-kengz
    Running setup.py install for box2d-kengz ... error
ERROR: Command errored out with exit status 1: /usr/bin/python3 -u -c 'import sys, setuptools, tokenize; sys.argv[0] = '"'"'/tmp/pip-install-n5mvt4j5/box2d-kengz/setup.py'"'"'; __file__='"'"'/tmp/pip-install-n5mvt4j5/box2d-kengz/setup.py'"'"';f=getattr(tokenize, '"'"'open'"'"', open)(__file__);code=f.read().replace('"'"'\r\n'"'"', '"'"'\n'"'"');f.close();exec(compile(code, __file__, '"'"'exec'"'"'))' install --record /tmp/pip-record-swug27pr/install-record.txt --single-version-externally-managed --compile Check the logs for full command output.


In [ ]:
import time, gym
import numpy as np
from tqdm import tqdm
import matplotlib.pyplot as plt
from itertools import count

In [ ]:
from pyvirtualdisplay import Display
from mitdeeplearning.lab3 import play_video
from gym.wrappers.monitoring.video_recorder import VideoRecorder

def save_video(env, model, name):
    display = Display(visible=0, size=(400, 300))
    display.start()

    filename = name + ".mp4"
    video_recorder = VideoRecorder(env, filename, enabled=True)
    
    counter = 0
    action = [0]
    done = 0
    obs = env.reset()
    while not done:
        env.render()
        video_recorder.capture_frame() 
        action = model(obs)
        obs, reward, done, info = env.step(action)
        counter += 1

    video_recorder.close()
    video_recorder.enabled = False
    print("Successfully saved {} frames into {}!".format(counter, filename))
    return filename

In [ ]:
env = gym.make('BipedalWalker-v3')
env.reset()

save_video(env, lambda x: [0]*4, 'a')
play_video('a.mp4')

/usr/local/lib/python3.7/dist-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
  warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))


Successfully saved 124 frames into a.mp4!


In [ ]:
state_dim = 24
action_dim = 4

#**Import Torch**

In [ ]:
import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
from torch.distributions.normal import Normal
from torch.nn.utils import clip_grad_value_


# if gpu is to be used
if torch.cuda.is_available():
  device = torch.device("cuda")
  torch.set_default_tensor_type(torch.cuda.FloatTensor)
else:
  device = torch.device("cpu")
  torch.set_default_tensor_type(torch.FloatTensor)

##Traininig utils

In [ ]:
def optimize(model, optimizer, loss, clip_value = 1):
    optimizer.zero_grad()
    loss.backward()
    clip_grad_value_(model.parameters(), clip_value)
    optimizer.step()

In [ ]:
def soft_update(target, source, tau):
	for a, b in zip(target.parameters(), source.parameters()):
		a.data.copy_(a.data * (1.0 - tau) + b.data * tau)

##Util to Plot reward


In [ ]:
from IPython import display as ipythondisplay

tic = time.time()
def plot(reward):
    global tic
    if time.time() - tic > 2:

      plt.cla()
      plt.plot(reward)
      plt.xlabel('episodes')
      plt.ylabel('rewards')

      ipythondisplay.clear_output(wait=True)
      ipythondisplay.display(plt.gcf())
      tic = time.time()

#**Replay Memory**

In [ ]:
from recordclass import recordclass

Transitions = recordclass('Transitions', ('states', 'actions', 'next_states', 'rewards', 'dones'))

class ReplayMemory():
    def __init__(self, capacity = 1000, state_dim = 24, action_dim = 4):
      
        self.length = 0
        self.capacity = capacity

        self.states = np.zeros((capacity, state_dim))
        self.actions = np.zeros((capacity, action_dim))
        self.next_states = np.zeros((capacity, state_dim))
        self.rewards = np.zeros((capacity, 1))
        self.dones = np.zeros((capacity, 1))
      
    def add_transition(self, *args):
        index = self.length % self.capacity

        self.states[index] = args[0]
        self.actions[index] = args[1]
        self.next_states[index] = args[2]
        self.rewards[index] = args[3]
        self.dones[index] = args[4]

        self.length += 1

    def sample(self, batch_size):

        maxind = min(self.length, self.capacity)
        inds = np.random.choice(maxind, batch_size)

        batch = Transitions(self.states[inds],
                            self.actions[inds],
                            self.next_states[inds],
                            self.rewards[inds],
                            self.dones[inds])
        
        for i in range(5):
          batch[i] = torch.tensor(batch[i], dtype=torch.float)

        return batch
    
    def clear(self): 
      self.length = 0
        
    def __len__(self):
      return min(self.length, self.capacity)

#**Q-value Network**

In [ ]:
class DQN(nn.Module):

    def __init__(self, state_dim = 24, action_dim = 4):
        super(DQN, self).__init__()
        self.l11 = nn.Linear(state_dim, 64)
        self.l12 = nn.Linear(action_dim, 16)

        self.l2 = nn.Linear(80, 128)
        self.l3 = nn.Linear(128, 256)

        self.last = nn.Linear(256, 1)
        self.last.weight.data.uniform_(-0.05,0.05)
        self.last.bias.data.fill_(0.01)

    def forward(self, states, actions):
        x = torch.cat((self.l11(states), self.l12(actions)),1)
        x = F.silu(x)
        x = F.silu(self.l2(x))
        x = F.silu(self.l3(x))
        x = self.last(x)
        return x


#**Double Q-Network critic** 

In [ ]:
class Critic(nn.Module):
  def __init__(self, state_dim = 24, action_dim = 4):
    super(Critic, self).__init__()
    self.q1 = DQN(state_dim, action_dim)
    self.q2 = DQN(state_dim, action_dim)
  
  def predict(self, states, actions):
    q1 = self.q1(states, actions)
    q2 = self.q2(states, actions)
    return q1, q2
  
  def forward(self, states, actions):
    q1, q2 = self.predict(states, actions)
    return torch.min(q1, q2)
  
  def calc_loss(self, states, actions, expected_critic_values):
    q1, q2 = self.predict(states, actions)
    loss1 = F.smooth_l1_loss(expected_critic_values, q1)
    loss2 = F.smooth_l1_loss(expected_critic_values, q2)
    return loss1 + loss2
  
  def requires_grad(self, boolean = True):
    for param in self.parameters():
        param.requires_grad = boolean


#**Policy network**

In [ ]:
class Policy(nn.Module):

    def __init__(self, state_dim = 24, action_dim = 4):
        super(Policy, self).__init__()

        self.l1 = nn.Linear(state_dim, 64)
        self.l2 = nn.Linear(64, 128)
        self.l3 = nn.Linear(128, 256)

        self.mean_layer = nn.Linear(256, action_dim)
        self.mean_layer.weight.data.uniform_(-0.01,0.01)
        self.mean_layer.bias.data.fill_(0.01)

        self.log_std = nn.Linear(256, action_dim)
        self.log_std.weight.data.uniform_(-0.05,0.05)
        self.log_std.bias.data.fill_(0.01)


    def forward(self, states):

        x = F.silu(self.l1(states))
        x = F.silu(self.l2(x))
        x = F.silu(self.l3(x))

        mean = self.mean_layer(x)
        std = torch.exp(self.log_std(x).clamp(-20, 2))

        return Normal(mean, std)

    def sample(self, states):

        dist = self.forward(states)
        samples = dist.rsample()
        actions = torch.tanh(samples)
        log_probs = dist.log_prob(samples) - torch.log(1 - actions**2 + 1e-8)
        
        return actions, log_probs.mean(axis = 1)

    def choose_action(self, state, training = True):
        
        with torch.no_grad(): 
          state = torch.tensor(state, dtype = torch.float).unsqueeze(0)
          dist = self.forward(state)
          sample = dist.sample() if training else dist.mean
          action = torch.tanh(sample).squeeze(0)

        return np.round(action.cpu().numpy(), 5)       


#**Initialize**
###[Soft Actor-Critic](https://spinningup.openai.com/en/latest/algorithms/sac.html)

In [ ]:
gamma = 0.99   # discount factor
alpha = 0.1  # entropy reward coeff

actor = Policy().to(device)
critic = Critic().to(device)

target_critic = Critic().to(device)
target_critic.load_state_dict(critic.state_dict())

<All keys matched successfully>

In [ ]:
actor_optimizer  = optim.Adam(actor.parameters(), 1e-3)
critic_optimizer = optim.Adam(critic.parameters(), 1e-3)

In [ ]:
memory = ReplayMemory(300000)

In [ ]:
def save(name):
  torch.save({
            'actor': actor.state_dict(),
            'critic': target_critic.state_dict(),
            'actor_optimizer': actor_optimizer.state_dict(),
            'critic_optimizer': critic_optimizer.state_dict(),
            }, name)


#**Single training step**

In [ ]:
def train_step(batch_size = 64):

    batch = memory.sample(batch_size)

  #---------------------critic training----------------------------------
    with torch.no_grad(): 
      next_actions, log_probs = actor.sample(batch.next_states)
      next_critic_values = target_critic(batch.next_states, next_actions)
      expected_critic_values = batch.rewards + (1 - batch.dones)*gamma*(next_critic_values - alpha*log_probs)

    critic_loss = critic.calc_loss(batch.states, batch.actions, expected_critic_values)

    optimize(critic, critic_optimizer, critic_loss)
  #---------------------------------------------------------------------


   #---------------------actor training----------------------------------
    critic.requires_grad(False)

    actions, log_probs = actor.sample(batch.states)
    critic_value = critic(batch.states, actions)
    actor_loss = -torch.mean(critic_value - alpha*log_probs)

    optimize(actor, actor_optimizer, actor_loss)

    critic.requires_grad(True)
  #-----------------------------------------------------------------------


  #----------------soft update target critic--------------------------------
    soft_update(target_critic, critic, 0.005)
  #-------------------------------------------------------------------------

In [ ]:
reward_list = []
avg_rewards = []

#**Training**

In [ ]:
env = gym.make('BipedalWalker-v3')

for i_episode in tqdm(range(100)):

  state = env.reset()
  total_reward = 0
  done = 0
  steps = 0

  while not done:

    action = actor.choose_action(state)
    next_state, reward, done, info = env.step(action)
    memory.add_transition(state, action, next_state, reward, done)

    train_step()

    total_reward += reward
    state = next_state
    steps += 1

  reward_list.append(total_reward)
  avg_rewards.append(np.mean(reward_list[-40:])) 

  plot(avg_rewards)

In [ ]:
save('bestwalker')

In [ ]:
from google.colab import files
files.download('bestwalker') 

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
files.upload()

Saving bestwalker (7) to bestwalker (7)


{'bestwalker (7)': b'PK\x03\x04\x00\x00\x08\x08\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x10\x00\x12\x00archive/data.pklFB\x0e\x00ZZZZZZZZZZZZZZ\x80\x02}q\x00(X\x05\x00\x00\x00actorq\x01ccollections\nOrderedDict\nq\x02)Rq\x03(X\t\x00\x00\x00l1.weightq\x04ctorch._utils\n_rebuild_tensor_v2\nq\x05((X\x07\x00\x00\x00storageq\x06ctorch\nFloatStorage\nq\x07X\x01\x00\x00\x000q\x08X\x03\x00\x00\x00cpuq\tM\x00\x06tq\nQK\x00K@K\x18\x86q\x0bK\x18K\x01\x86q\x0c\x89h\x02)Rq\rtq\x0eRq\x0fX\x07\x00\x00\x00l1.biasq\x10h\x05((h\x06h\x07X\x01\x00\x00\x001q\x11h\tK@tq\x12QK\x00K@\x85q\x13K\x01\x85q\x14\x89h\x02)Rq\x15tq\x16Rq\x17X\t\x00\x00\x00l2.weightq\x18h\x05((h\x06h\x07X\x01\x00\x00\x002q\x19h\tM\x00 tq\x1aQK\x00K\x80K@\x86q\x1bK@K\x01\x86q\x1c\x89h\x02)Rq\x1dtq\x1eRq\x1fX\x07\x00\x00\x00l2.biasq h\x05((h\x06h\x07X\x01\x00\x00\x003q!h\tK\x80tq"QK\x00K\x80\x85q#K\x01\x85q$\x89h\x02)Rq%tq&Rq\'X\t\x00\x00\x00l3.weightq(h\x05((h\x06h\x07X\x01\x00\x00\x004q)h\tM\x00\x80tq*Q

In [ ]:
!ls

In [ ]:
state = torch.load('bestwalker (7)', map_location = device)

In [ ]:
actor.load_state_dict(state['actor'])
critic.load_state_dict(state['critic'])
actor_optimizer.load_state_dict(state['actor_optimizer'])
critic_optimizer.load_state_dict(state['critic_optimizer'])

target_critic.load_state_dict(critic.state_dict())

<All keys matched successfully>

#Test Learned Policy

In [ ]:
# env1 = gym.make('BipedalWalker-v3')
env.reset()

array([ 2.74562370e-03,  1.17593247e-05, -1.53336558e-03, -1.60000753e-02,
        9.25276130e-02,  3.55962105e-03,  8.59748527e-01, -1.42761910e-03,
        1.00000000e+00,  3.28331329e-02,  3.55946552e-03,  8.53515208e-01,
       -2.42197420e-03,  1.00000000e+00,  4.40813303e-01,  4.45819408e-01,
        4.61422026e-01,  4.89549398e-01,  5.34101903e-01,  6.02460027e-01,
        7.09147751e-01,  8.85930359e-01,  1.00000000e+00,  1.00000000e+00])

In [ ]:
policy = lambda x: actor.choose_action(x, False)

In [ ]:
save_video(env, policy , 'a')
play_video('a.mp4')

Successfully saved 771 frames into a.mp4!
